In [0]:
def file_exists(path):
  try:
    dbutils.fs.ls(path)
    return True 
  except Exception as e:
    if 'java.io.FileNotFoundException' in str(e):
      return False
    else:
      raise

In [0]:
actorsUrl = "https://raw.githubusercontent.com/cegladanych/azure_bi_data/main/IMDB_movies/actors.csv"
filePath = "/FileStore/tables/Files/"
dbutils.fs.mkdirs(filePath)
actorsFile = "actors.csv"
tmp = "file:/tmp/"
dbfsdestination = "dbfs:/FileStore/tables/Files/"

# Read DataFrame with Schema

In [0]:
import urllib.request

if (file_exists(filePath + actorsFile) == False):
  urllib.request.urlretrieve(actorsUrl,"/tmp/" + actorsFile)
  dbutils.fs.mv(tmp + actorsFile,dbfsdestination + actorsFile)

In [0]:
filePath = "dbfs:/FileStore/tables/Files/actors.csv"
actorsDf = spark.read.format("csv") \
            .option("header","true") \
            .option("inferSchema","true") \
            .load(filePath)

In [0]:
from pyspark.sql.types import StructType, StructField, IntegerType, StringType

actors_schema = StructType([
    StructField("imdb_title_id", StringType(), False),
    StructField("ordering", IntegerType(), True),
    StructField("imb_name_id", StringType(), True),
    StructField("category", StringType(), True),
    StructField("job", StringType(), True),
    StructField("characters", StringType(), True),
])

In [0]:
actorsWithSchema = spark.read.format("csv") \
            .option("header","true") \
            .option("inferSchema","true") \
            .schema(actors_schema) \
            .load(filePath) 

actorsWithSchema.printSchema()

root
 |-- imdb_title_id: string (nullable = true)
 |-- ordering: integer (nullable = true)
 |-- imb_name_id: string (nullable = true)
 |-- category: string (nullable = true)
 |-- job: string (nullable = true)
 |-- characters: string (nullable = true)



In [0]:
actorsWithSchema.show()

+-------------+--------+-----------+---------------+----------+--------------------+
|imdb_title_id|ordering|imb_name_id|       category|       job|          characters|
+-------------+--------+-----------+---------------+----------+--------------------+
|    tt0000009|       1|  nm0063086|        actress|      null|[Miss Geraldine H...|
|    tt0000009|       2|  nm0183823|          actor|      null|      [Mr. Hamilton]|
|    tt0000009|       3|  nm1309758|          actor|      null|[Chauncey Depew -...|
|    tt0000009|       4|  nm0085156|       director|      null|                null|
|    tt0000574|       1|  nm0846887|        actress|      null|        [Kate Kelly]|
|    tt0000574|       2|  nm0846894|          actor|      null|     [School Master]|
|    tt0000574|       3|  nm3002376|          actor|      null|        [Steve Hart]|
|    tt0000574|       4|  nm0170118|        actress|      null|                null|
|    tt0000574|       5|  nm0846879|       director|      null|  

# Read Modes

Wykorzystaj posiadane pliki bądź użyj nowe.  Użyj Sparka do odczytania jednego pliku i użyj wszystkich typów read modes. Poprawny plik nie wywoła żadnych efektów, więc popsuj dane tak aby każda z read modes zadziałał.

In [0]:
# Corrupt data
from pyspark.sql import SparkSession

df = spark.read.format("csv") \
    .option("header", "true") \
    .option("inferSchema", "true") \
    .load(filePath)

from pyspark.sql.functions import when

df = df.withColumn("ordering", when(df["ordering"] == 4, "xyz"))

df.show()

+-------------+--------+------------+---------------+----------+--------------------+
|imdb_title_id|ordering|imdb_name_id|       category|       job|          characters|
+-------------+--------+------------+---------------+----------+--------------------+
|    tt0000009|    null|   nm0063086|        actress|      null|[Miss Geraldine H...|
|    tt0000009|    null|   nm0183823|          actor|      null|      [Mr. Hamilton]|
|    tt0000009|    null|   nm1309758|          actor|      null|[Chauncey Depew -...|
|    tt0000009|     xyz|   nm0085156|       director|      null|                null|
|    tt0000574|    null|   nm0846887|        actress|      null|        [Kate Kelly]|
|    tt0000574|    null|   nm0846894|          actor|      null|     [School Master]|
|    tt0000574|    null|   nm3002376|          actor|      null|        [Steve Hart]|
|    tt0000574|     xyz|   nm0170118|        actress|      null|                null|
|    tt0000574|    null|   nm0846879|       director| 

In [0]:
print(filePath)

dbfs:/FileStore/tables/Files/actors.csv


In [0]:
output_path = 'dbfs:/FileStore/tables/Files/actors_corrupted.csv'

df.write.mode("overwrite") \
    .option("header", "true") \
    .csv(output_path)

In [0]:
filePath_corrupted = "dbfs:/FileStore/tables/Files/actors_corrupted.csv"

actorsWithSchema = spark.read.format("csv") \
            .option("header","true") \
            .option("inferSchema","true") \
            .schema(actors_schema) \
            .option("mode", "DROPMALFORMED") \
            .load(filePath_corrupted) 

display(actorsWithSchema)

imdb_title_id ordering imb_name_id category job characters tt0000009 null nm0063086 actress null [Miss Geraldine Holbrook (Miss Jerry)] tt0000009 null nm0183823 actor null [Mr. Hamilton] tt0000009 null nm1309758 actor null [Chauncey Depew - the Director of the New York Central Railroad] tt0000574 null nm0846887 actress null [Kate Kelly] tt0000574 null nm0846894 actor null [School Master] tt0000574 null nm3002376 actor null [Steve Hart] tt0000574 null nm0846879 director null null tt0000574 null nm0317210 producer producer null tt0000574 null nm0425854 producer producer null tt0000574 null nm0846911 producer producer null tt0000574 null nm2421834 composer null null tt0000574 null nm0675239 cinematographer null null tt0001892 null nm0003425 actress null [Stella] tt0001892 null nm0699637 actor null [Grev Johan Waldberg] tt0001892 null nm0375839 actor null [Hofjuveler A. Hirsch] tt0001892 null nm0300487 director null null tt0001892 null nm2131092 writer screenplay null tt0001892 null nm0423762 cinematographer null null tt0001892 null nm0005869 cinematographer null null tt0001892 null nm0282348 actor null null tt0001892 null nm2325688 actress null null tt0002101 null nm0306947 actress null [Cleopatra - Queen of Egypt] tt0002101 null nm0801774 actress null [Iras - An Attendant] tt0002101 null nm0276160 actress null [Charmian - An Attendant] tt0002101 null nm0309130 director null null tt0002101 null nm0765026 writer adapted from the play by null tt0002101 null nm0182557 actress null [Nicola - a Child] tt0002101 null nm1950505 actor null [Antony - a Triumvir and General] tt0002101 null nm0397513 actor null [Pharon - a Greek Slave and Fisherman] tt0002101 null nm0906610 actor null [Venditius - a Roman Soldier] tt0002130 null nm0660139 actor null [Dante Alighieri] tt0002130 null nm0685283 actor null [Virgilio] tt0002130 null nm0209738 actor null [Farinata degli Uberti,Pier delle Vigne,Il conte Ugolino] tt0002130 null nm0078205 director null null tt0002130 null nm0655824 director null null tt0002130 null nm0019604 writer poem La Divina Commedia null tt0002130 null nm1374692 composer null null tt0002130 null nm1376296 cinematographer null null tt0002130 null nm1376180 production_designer null null tt0002199 null nm0087381 actor null [Jesus - the Man] tt0002199 null nm0245769 actor null [Jesus as a Youth] tt0002199 null nm0310155 actress null [Mary] tt0002199 null nm0646058 director null null tt0002199 null nm0391228 cinematographer null null tt0002199 null nm0605017 actor null [Pilate] tt0002199 null nm0014707 actor null [John the Baptist] tt0002199 null nm0897085 actor null [Judas] tt0002199 null nm0446092 actor null [Herod] tt0002423 null nm0624470 actress null [Jeanne Vaubernier - later Madame Dubarry] tt0002423 null nm0417837 actor null [König Louis XV] tt0002423 null nm0509573 actor null [Armand De Foix] tt0002423 null nm0523932 director null null tt0002423 null nm0266183 writer null null tt0002423 null nm0473134 writer writer null tt0002423 null nm0203452 producer producer null tt0002423 null nm0005882 cinematographer null null tt0002423 null nm0913298 cinematographer null null tt0002445 null nm0637019 actor null [Vinicius] tt0002445 null nm0784988 actor null [Petronius] tt0002445 null nm0146335 actor null [Nero] tt0002445 null nm0345500 director null null tt0002445 null nm0797197 writer novel null tt0002445 null nm1113433 cinematographer null null tt0002445 null nm0093646 cinematographer null null tt0002445 null nm0409208 production_designer null null tt0002452 null nm0218404 actor null [Carol I] tt0002452 null nm2386325 actress null [Principesa Elisabeta] tt0002452 null nm0636620 actor null [Osman Pasa] tt0002452 null nm0108345 director null null tt0002452 null nm2384492 writer screenplay null tt0002452 null nm0691238 producer producer null tt0002452 null nm0199554 cinematographer null null tt0002461 null nm0312600 actor null [King Edward IV] tt0002461 null nm0911963 actor null [Richard, Duke of Gloucester, afterward Richard III] t

In [0]:
actorsWithSchema = spark.read.format("csv") \
            .option("header","true") \
            .option("inferSchema","true") \
            .schema(actors_schema) \
            .option("mode", "PERMISSIVE") \
            .load(filePath_corrupted) 

display(actorsWithSchema)

imdb_title_id ordering imb_name_id category job characters tt0000009 null nm0063086 actress null [Miss Geraldine Holbrook (Miss Jerry)] tt0000009 null nm0183823 actor null [Mr. Hamilton] tt0000009 null nm1309758 actor null [Chauncey Depew - the Director of the New York Central Railroad] tt0000009 null nm0085156 director null null tt0000574 null nm0846887 actress null [Kate Kelly] tt0000574 null nm0846894 actor null [School Master] tt0000574 null nm3002376 actor null [Steve Hart] tt0000574 null nm0170118 actress null null tt0000574 null nm0846879 director null null tt0000574 null nm0317210 producer producer null tt0000574 null nm0425854 producer producer null tt0000574 null nm0846911 producer producer null tt0000574 null nm2421834 composer null null tt0000574 null nm0675239 cinematographer null null tt0001892 null nm0003425 actress null [Stella] tt0001892 null nm0699637 actor null [Grev Johan Waldberg] tt0001892 null nm0375839 actor null [Hofjuveler A. Hirsch] tt0001892 null nm0016799 actor null null tt0001892 null nm0300487 director null null tt0001892 null nm2131092 writer screenplay null tt0001892 null nm0423762 cinematographer null null tt0001892 null nm0005869 cinematographer null null tt0001892 null nm0282348 actor null null tt0001892 null nm2325688 actress null null tt0002101 null nm0306947 actress null [Cleopatra - Queen of Egypt] tt0002101 null nm0801774 actress null [Iras - An Attendant] tt0002101 null nm0276160 actress null [Charmian - An Attendant] tt0002101 null nm0733482 actress null [Octavia - Wife of Antony] tt0002101 null nm0309130 director null null tt0002101 null nm0765026 writer adapted from the play by null tt0002101 null nm0182557 actress null [Nicola - a Child] tt0002101 null nm1950505 actor null [Antony - a Triumvir and General] tt0002101 null nm0397513 actor null [Pharon - a Greek Slave and Fisherman] tt0002101 null nm0906610 actor null [Venditius - a Roman Soldier] tt0002130 null nm0660139 actor null [Dante Alighieri] tt0002130 null nm0685283 actor null [Virgilio] tt0002130 null nm0209738 actor null [Farinata degli Uberti,Pier delle Vigne,Il conte Ugolino] tt0002130 null nm3942815 actor null [Il conte Ugolino] tt0002130 null nm0078205 director null null tt0002130 null nm0655824 director null null tt0002130 null nm0019604 writer poem La Divina Commedia null tt0002130 null nm1374692 composer null null tt0002130 null nm1376296 cinematographer null null tt0002130 null nm1376180 production_designer null null tt0002199 null nm0087381 actor null [Jesus - the Man] tt0002199 null nm0245769 actor null [Jesus as a Youth] tt0002199 null nm0310155 actress null [Mary] tt0002199 null nm0391220 actress null [Mary Magdalene] tt0002199 null nm0646058 director null null tt0002199 null nm0391228 cinematographer null null tt0002199 null nm0605017 actor null [Pilate] tt0002199 null nm0014707 actor null [John the Baptist] tt0002199 null nm0897085 actor null [Judas] tt0002199 null nm0446092 actor null [Herod] tt0002423 null nm0624470 actress null [Jeanne Vaubernier - later Madame Dubarry] tt0002423 null nm0417837 actor null [König Louis XV] tt0002423 null nm0509573 actor null [Armand De Foix] tt0002423 null nm0903235 actor null [Graf Jean Dubarry] tt0002423 null nm0523932 director null null tt0002423 null nm0266183 writer null null tt0002423 null nm0473134 writer writer null tt0002423 null nm0203452 producer producer null tt0002423 null nm0005882 cinematographer null null tt0002423 null nm0913298 cinematographer null null tt0002445 null nm0637019 actor null [Vinicius] tt0002445 null nm0784988 actor null [Petronius] tt0002445 null nm0146335 actor null [Nero] tt0002445 null nm0146331 actress null [Eunice] tt0002445 null nm0345500 director null null tt0002445 null nm0797197 writer novel null tt0002445 null nm1113433 cinematographer null null tt0002445 null nm0093646 cinematographer null null tt0002445 null nm0409208 production_designer null null tt0002452 null nm0218404 actor null [Carol I] tt0002452 null nm2386325 actress null 

In [0]:
actorsWithSchema = spark.read.format("csv") \
            .option("header","true") \
            .option("inferSchema","true") \
            .schema(actors_schema) \
            .option("mode", "FAILFAST") \
            .load(filePath_corrupted) 

display(actorsWithSchema)

org.apache.spark.SparkException: Job aborted due to stage failure: Task 0 in stage 19.0 failed 1 times, most recent failure: Lost task 0.0 in stage 19.0 (TID 47) (ip-10-172-186-210.us-west-2.compute.internal executor driver): com.databricks.sql.io.FileReadException: Error while reading file dbfs:/FileStore/tables/Files/actors_corrupted.csv/part-00000-tid-6137145950919010644-8d16d06d-9581-4039-88df-5ab79ce71f93-37-1-c000.csv.
	at org.apache.spark.sql.execution.datasources.FileScanRDD$$anon$1$$anon$2.logFileNameAndThrow(FileScanRDD.scala:704)
	at org.apache.spark.sql.execution.datasources.FileScanRDD$$anon$1$$anon$2.getNext(FileScanRDD.scala:673)
	at org.apache.spark.util.NextIterator.hasNext(NextIterator.scala:73)
	at org.apache.spark.sql.execution.datasources.FileScanRDD$$anon$1.$anonfun$hasNext$1(FileScanRDD.scala:493)
	at scala.runtime.java8.JFunction0$mcZ$sp.apply(JFunction0$mcZ$sp.java:23)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.sql.execution.datasources.FileScanRDD$$anon$1.hasNext(FileScanRDD.scala:486)
	at scala.collection.Iterator$$anon$10.hasNext(Iterator.scala:460)
	at org.apache.spark.sql.execution.collect.UnsafeRowBatchUtils$.encodeUnsafeRows(UnsafeRowBatchUtils.scala:82)
	at org.apache.spark.sql.execution.collect.Collector.$anonfun$processFunc$1(Collector.scala:208)
	at org.apache.spark.scheduler.ResultTask.$anonfun$runTask$3(ResultTask.scala:75)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.ResultTask.$anonfun$runTask$1(ResultTask.scala:75)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.ResultTask.runTask(ResultTask.scala:55)
	at org.apache.spark.scheduler.Task.doRunTask(Task.scala:179)
	at org.apache.spark.scheduler.Task.$anonfun$run$5(Task.scala:142)
	at com.databricks.unity.EmptyHandle$.runWithAndClose(UCSHandle.scala:126)
	at org.apache.spark.scheduler.Task.$anonfun$run$1(Task.scala:142)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.Task.run(Task.scala:97)
	at org.apache.spark.executor.Executor$TaskRunner.$anonfun$run$13(Executor.scala:904)
	at org.apache.spark.util.Utils$.tryWithSafeFinally(Utils.scala:1741)
	at org.apache.spark.executor.Executor$TaskRunner.$anonfun$run$4(Executor.scala:907)
	at scala.runtime.java8.JFunction0$mcV$sp.apply(JFunction0$mcV$sp.java:23)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.executor.Executor$TaskRunner.run(Executor.scala:761)
	at java.util.concurrent.ThreadPoolExecutor.runWorker(ThreadPoolExecutor.java:1149)
	at java.util.concurrent.ThreadPoolExecutor$Worker.run(ThreadPoolExecutor.java:624)
	at java.lang.Thread.run(Thread.java:750)
Caused by: org.apache.spark.SparkException: Malformed records are detected in record parsing. Parse Mode: FAILFAST. To process malformed records as null result, try setting the option 'mode' as 'PERMISSIVE'.
	at org.apache.spark.sql.errors.QueryExecutionErrors$.malformedRecordsDetectedInRecordParsingError(QueryExecutionErrors.scala:1936)
	at org.apache.spark.sql.catalyst.util.FailureSafeParser.parse(FailureSafeParser.scala:103)
	at org.apache.spark.sql.catalyst.csv.UnivocityParser$.$anonfun$parseIterator$2(UnivocityParser.scala:507)
	at scala.collection.Iterator$$anon$11.nextCur(Iterator.scala:486)
	at scala.collection.Iterator$$anon$11.hasNext(Iterator.scala:492)
	at org.apache.spark.util.CompletionIterator.hasNext(CompletionIterator.scala:31)
	at scala.collection.Iterator$$anon$10.hasNext(Iterator.scala:460)
	at org.apache.spark.sql.execution.datasources.FileScanRDD$$anon$1$$anon$2.getNext(FileScanRDD.scala:619)
	... 28 more
Caused by: org.apache.spark.sql.catalyst.util.BadRecordException: java.lang.NumberFormatException: For input string: "xyz"
Caused by: java.lang.NumberFor

# Save to JSON and check with DataFrameReader

In [0]:
actorsWithSchema.write.mode("overwrite") \
    .json("dbfs:/FileStore/tables/Files/actors.json")

actorsWithSchema.show()

+-------------+--------+-----------+---------------+----------+--------------------+
|imdb_title_id|ordering|imb_name_id|       category|       job|          characters|
+-------------+--------+-----------+---------------+----------+--------------------+
|    tt0000009|    null|  nm0063086|        actress|      null|[Miss Geraldine H...|
|    tt0000009|    null|  nm0183823|          actor|      null|      [Mr. Hamilton]|
|    tt0000009|    null|  nm1309758|          actor|      null|[Chauncey Depew -...|
|    tt0000009|    null|  nm0085156|       director|      null|                null|
|    tt0000574|    null|  nm0846887|        actress|      null|        [Kate Kelly]|
|    tt0000574|    null|  nm0846894|          actor|      null|     [School Master]|
|    tt0000574|    null|  nm3002376|          actor|      null|        [Steve Hart]|
|    tt0000574|    null|  nm0170118|        actress|      null|                null|
|    tt0000574|    null|  nm0846879|       director|      null|  

In [0]:
read_df = spark.read.format("json").load("dbfs:/FileStore/tables/Files/actors.json")
display(read_df)

category characters imb_name_id imdb_title_id job actor [Tom] nm6005417 tt3249124 null director null nm1871431 tt3249124 null producer null nm1862032 tt3249124 producer composer null nm4261282 tt3249124 null production_designer null nm1677303 tt3249124 null actor [Sebastian] nm2946712 tt3249158 null actress [Miranda] nm2578315 tt3249158 null actor [Jacinto] nm7033017 tt3249158 null actor [Rosa] nm7033021 tt3249158 null director null nm1848095 tt3249158 null producer null nm1120960 tt3249158 producer producer null nm4065853 tt3249158 producer producer null nm1680580 tt3249158 producer composer null nm2613542 tt3249158 null cinematographer null nm0608209 tt3249158 null actress [Polly] nm2768721 tt3249524 null actress [Rachel] nm0059088 tt3249524 null actress [Rachel] nm6005667 tt3249524 null actor [Bigg Weezy] nm6736174 tt3249524 null director null nm1053523 tt3249524 null writer null nm2947593 tt3249524 null writer null nm1407022 tt3249524 null producer null nm3322517 tt3249524 producer producer null nm1698040 tt3249524 producer producer null nm1065316 tt3249524 producer actor [Eli McAllister] nm3019095 tt3250032 null actor [Sean McAllister] nm0004978 tt3250032 null actress [Woman in Suit] nm3352882 tt3250032 null actress [Woman in Trench Coat] nm2416315 tt3250032 null director null nm0001824 tt3250032 null producer null nm0210348 tt3250032 producer producer null nm0711910 tt3250032 producer producer null nm2521250 tt3250032 producer composer null nm1650518 tt3250032 null composer null nm0284935 tt3250032 null actress [Sophie] nm0336701 tt3250650 null actor [Alex] nm0645803 tt3250650 null actor [Mateo] nm0173997 tt3250650 null actor [Elias] nm3528675 tt3250650 null director null nm5831383 tt3250650 null writer null nm3403118 tt3250650 writer producer null nm2498510 tt3250650 producer composer null nm2945256 tt3250650 null cinematographer null nm2972954 tt3250650 director of photography editor null nm0524552 tt3250650 null actor [Tokió's younger brother] nm6055407 tt3251284 null actor [Tokió] nm4705978 tt3251284 null actress [Eszter] nm6007461 tt3251284 null actor [Peti] nm6007460 tt3251284 null director null nm0077218 tt3251284 null writer null nm0457108 tt3251284 writer producer null nm3200712 tt3251284 producer composer null nm1473056 tt3251284 null cinematographer null nm0843988 tt3251284 null editor null nm0891966 tt3251284 null actor [Rebel] nm6401595 tt3251306 null actress [Maid] nm6787262 tt3251306 null actress [Maid] nm6787263 tt3251306 null actor [King Henry II] nm6579570 tt3251306 null director null nm3375413 tt3251306 null writer null nm2780927 tt3251306 writer producer null nm5470262 tt3251306 producer producer null nm1486721 tt3251306 producer composer null nm3816365 tt3251306 null cinematographer null nm3934987 tt3251306 null actor [Robert Lang] nm1910274 tt3252594 null actor [Harry Lang] nm0001520 tt3252594 null actress [Sara-Beth] nm2439111 tt3252594 null actor [Lenny] nm2906174 tt3252594 null director null nm3337144 tt3252594 null producer null nm2777236 tt3252594 producer producer null nm0363958 tt3252594 producer producer null nm4408537 tt3252594 producer producer null nm3278307 tt3252594 producer producer null nm3696797 tt3252594 producer actress [Scout Havers] nm2061375 tt3252998 null actor [Sam Prescott] nm3306943 tt3252998 null actress [Tallulah 'Lulu' Havers] nm4115623 tt3252998 null actress [Gloria Prescott] nm0005412 tt3252998 null director null nm0920679 tt3252998 null producer null nm1762122 tt3252998 producer producer null nm2370243 tt3252998 producer producer null nm1164858 tt3252998 producer composer null nm0236757 tt3252998 null cinematographer null nm1946731 tt3252998 null actor [Matthew Taylor] nm0005245 tt3253232 null actress [Kristin Peralta] nm1229204 tt3253232 null actor [Terry Jackson] nm0004740 tt3253232 null actress [Aleya Taylor] nm5173848 tt3253232 null director null nm0216459 tt3253232 null writer null nm1226077 tt3253232 written by writer null nm6043491 tt3253232 written by producer 